In [4]:
# Download the dataset
!wget https://www.gutenberg.org/cache/epub/45/pg45.txt
!wget https://www.gutenberg.org/cache/epub/75982/pg75982.txt
!wget https://www.gutenberg.org/cache/epub/75979/pg75979.txt
!wget https://www.gutenberg.org/cache/epub/75978/pg75978.txt

--2025-04-29 17:57:26--  https://www.gutenberg.org/cache/epub/45/pg45.txt
Resolving www.gutenberg.org (www.gutenberg.org)... 152.19.134.47, 2610:28:3090:3000:0:bad:cafe:47
Connecting to www.gutenberg.org (www.gutenberg.org)|152.19.134.47|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 606737 (593K) [text/plain]
Saving to: ‘pg45.txt.3’

pg45.txt.3          100%[===================>] 592.52K  --.-KB/s    in 0.1s    

2025-04-29 17:57:31 (5.26 MB/s) - ‘pg45.txt.3’ saved [606737/606737]

--2025-04-29 17:57:31--  https://www.gutenberg.org/cache/epub/75982/pg75982.txt
Resolving www.gutenberg.org (www.gutenberg.org)... 152.19.134.47, 2610:28:3090:3000:0:bad:cafe:47
Connecting to www.gutenberg.org (www.gutenberg.org)|152.19.134.47|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 990773 (968K) [text/plain]
Saving to: ‘pg75982.txt.2’

pg75982.txt.2       100%[===================>] 967.55K  --.-KB/s    in 0.1s    

2025-04-29 17:57:32 (9.91 MB/s)

In [99]:
# Read and concatenate the datasets
text_files = ['pg45.txt.3', 'pg75982.txt.2', 'pg75979.txt.1','pg75978.txt', 'pg45.txt.3', 'pg75982.txt.2', 'pg75979.txt.1','pg75978.txt', 'pg45.txt.3', 'pg75982.txt.2', 'pg75979.txt.1','pg75978.txt', 'pg45.txt.3', 'pg75982.txt.2', 'pg75979.txt.1','pg75978.txt']
combined_text = ''

for file in text_files:
  with open(file, 'r', encoding='utf-8') as f:
    combined_text += f.read() + '\n'

print(f"Total length of combined dataset: {len(combined_text)} characters")

Total length of combined dataset: 9045344 characters


In [100]:
import re

combined_text = combined_text.lower()
combined_text = re.sub('[^a-z0-9]', ' ', combined_text)
combined_text = re.sub('\s+', ' ', combined_text).strip()

In [101]:
combined_text

'the project gutenberg ebook of anne of green gables this ebook is for the use of anyone anywhere in the united states and most other parts of the world at no cost and with almost no restrictions whatsoever you may copy it give it away or re use it under the terms of the project gutenberg license included with this ebook or online at www gutenberg org if you are not located in the united states you will have to check the laws of the country where you are located before using this ebook title anne of green gables author l m montgomery release date june 27 2008 ebook 45 most recently updated april 29 2025 language english credits david widger and charles keller start of the project gutenberg ebook anne of green gables anne of green gables by lucy maud montgomery table of contents chapter i mrs rachel lynde is surprised chapter ii matthew cuthbert is surprised chapter iii marilla cuthbert is surprised chapter iv morning at green gables chapter v anne s history chapter vi marilla makes up 

In [102]:
# Here are all the unique characters that occur in this text
chars = sorted(list(set(combined_text)))
vocab_size = len(chars)
print(''.join(chars))
print(vocab_size)

 0123456789abcdefghijklmnopqrstuvwxyz
37


In [103]:
# Create a mapping from characters to integers and vice versa
ctoi = {char:index for index,char in enumerate(chars)}
itoc = {index:char for index,char in enumerate(chars)}
encode = lambda s: [ctoi[char] for char in s]
decode = lambda l: ''.join([itoc[index] for index in l])

In [104]:
print(encode("llms are awesome"))

[22, 22, 23, 29, 0, 11, 28, 15, 0, 11, 33, 15, 29, 25, 23, 15]


In [105]:
# Let's now encode the entire text dataset and store it into a torch.tensor
import torch
data = torch.tensor(encode(combined_text), dtype=torch.long)

In [106]:
print(data.shape, data.dtype)

torch.Size([8670735]) torch.int64


In [107]:
training_len = int(0.9*len(data))
train_data = data[:training_len]
val_data = data[training_len:]

In [133]:
block_size = 16

In [134]:
x = train_data[:block_size]
y = train_data[1:block_size+1]
for token in range(block_size):
  context = x[:token+1]
  target = y[token]
  print(f"When input is {context}, the target is {target}")

When input is tensor([30]), the target is 18
When input is tensor([30, 18]), the target is 15
When input is tensor([30, 18, 15]), the target is 0
When input is tensor([30, 18, 15,  0]), the target is 26
When input is tensor([30, 18, 15,  0, 26]), the target is 28
When input is tensor([30, 18, 15,  0, 26, 28]), the target is 25
When input is tensor([30, 18, 15,  0, 26, 28, 25]), the target is 20
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20]), the target is 15
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15]), the target is 13
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15, 13]), the target is 30
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15, 13, 30]), the target is 0
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15, 13, 30,  0]), the target is 17
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15, 13, 30,  0, 17]), the target is 31
When input is tensor([30, 18, 15,  0, 26, 28, 25, 20, 15, 13, 30,  0, 17, 31]), the target is 30
When inp

In [135]:
torch.manual_seed(42)
batch_size = 4 # B: how many independent sequences will we process in parallel?
block_size = 16 # T: what is the maximum context length for predictions?

# Generate a small batch of data of inputs x and targets y
def get_batch(split):
  data = train_data if split == 'train' else val_data
  index = torch.randint(len(data) - block_size, (batch_size,))
  x = torch.stack([data[i:i+block_size] for i in index])
  y = torch.stack([data[i+1:i+block_size+1] for i in index])
  return x, y

In [136]:
x_batch, y_batch = get_batch('train')
print('Inputs:')
print(x_batch.shape)
print(x_batch)
print('Targets:')
print(y_batch.shape)
print(y_batch)

Inputs:
torch.Size([4, 16])
tensor([[14,  0, 18, 19, 29,  0, 33, 15, 22, 22,  0, 21, 24, 25, 33, 24],
        [16,  0, 19, 23, 23, 15, 14, 19, 11, 30, 15, 22, 35,  0, 19, 16],
        [ 0, 18, 11, 14,  0, 18, 15,  0, 23, 25, 24, 15, 35,  0, 11, 24],
        [15, 24, 15, 28, 25, 29, 19, 30, 35,  0, 33, 18, 15, 24,  0, 29]])
Targets:
torch.Size([4, 16])
tensor([[ 0, 18, 19, 29,  0, 33, 15, 22, 22,  0, 21, 24, 25, 33, 24,  0],
        [ 0, 19, 23, 23, 15, 14, 19, 11, 30, 15, 22, 35,  0, 19, 16,  0],
        [18, 11, 14,  0, 18, 15,  0, 23, 25, 24, 15, 35,  0, 11, 24, 14],
        [24, 15, 28, 25, 29, 19, 30, 35,  0, 33, 18, 15, 24,  0, 29, 18]])


In [137]:
import torch
import torch.nn as nn
from torch.nn import functional as F
torch.manual_seed(42)

In [138]:
class BigramLM(nn.Module):
  def __init__(self, vocab_size):
    super().__init__()
    # Each token directly reads off the logits for the next token from a lookup table
    self.token_embedding_table = nn.Embedding(vocab_size, vocab_size)

  def forward(self, index, targets=None):
    # B = Batch, T = Time, C = Channel (vocab_size)
    # Index and targets are both (B,T) tensors of integers
    logits = self.token_embedding_table(index) # (B,T,C)

    if targets is None:
      loss = None
    else:
      B, T, C = logits.shape
      logits = logits.view(B*T, C) # Stretching out the tensor into B*T with size C because that's what Pytorch wants to see
      targets = targets.view(B*T)
      loss = F.cross_entropy(logits, targets)

    return logits,loss

  def generate(self, index, max_new_tokens):
    # Index is (B,T) array of indices in the current context
    for _ in range(max_new_tokens):
      # Get the predictions
      logits, loss = self(index)  # loss here will be ignored
      # Focus only on the last time step
      logits = logits[:, -1, :]
      # Apply softmax to get probabilities
      probs = F.softmax(logits, dim=-1)
      # Sample from the distribution
      index_next = torch.multinomial(probs, num_samples=1)
      # Append sampled index to the running sequence
      index = torch.cat((index, index_next), dim=1)
    return index

In [139]:
model = BigramLM(vocab_size)
logits, loss = model(x_batch, y_batch)
print(logits.shape)
print(loss)

torch.Size([64, 37])
tensor(4.1960, grad_fn=<NllLossBackward0>)


In [140]:
firstindex = torch.zeros((1,1), dtype=torch.long)
generated_indices = model.generate(index=firstindex, max_new_tokens=100)[0].tolist()
print(decode(generated_indices))

 36fs3vms46p336v1ylchkdvb1dwzr5glmipvty8b091a76levix8akmoh58rr9km1jqaa7lr91uqkvmywx63oa11npfotlxrn177


In [141]:
optimizer = torch.optim.AdamW(model.parameters(), lr=1e-3)

In [142]:
for steps in range(20000):
  # Sample a batch of data
  x_batch, y_batch = get_batch('train')

  # Evaluate the loss
  logits, loss = model(x_batch, y_batch)
  optimizer.zero_grad(set_to_none=True)
  loss.backward()
  optimizer.step()
  if steps % 1000 == 0:
    print(f"Interation {steps}: loss {loss.item():.4f}")

Interation 0: loss 4.1683
Interation 1000: loss 3.2854
Interation 2000: loss 3.0528
Interation 3000: loss 2.5166
Interation 4000: loss 2.5174
Interation 5000: loss 2.2465
Interation 6000: loss 2.5275
Interation 7000: loss 2.4103
Interation 8000: loss 2.4652
Interation 9000: loss 2.1090
Interation 10000: loss 2.4284
Interation 11000: loss 2.1808
Interation 12000: loss 2.1793
Interation 13000: loss 2.3072
Interation 14000: loss 2.3221
Interation 15000: loss 2.2175
Interation 16000: loss 2.2964
Interation 17000: loss 2.2695
Interation 18000: loss 2.4765
Interation 19000: loss 2.2945


In [92]:
firstindex = torch.zeros((1,1), dtype=torch.long)
generated_indices = model.generate(index=firstindex, max_new_tokens=1000)[0].tolist()
print(decode(generated_indices))

 murer d mad h ongtheatrouf ad akiny t cedert inthisored 1re thorlke mene t s d d f f eck ayushen miear ar may uin k cim cand tes hirt aioopr ghee 41 se wirs mn plan hanormenule th hoy he o limelingind arobes ds yaf wor thabas ge one heared con pis ly m ci o iss g y s af tong alissag e mig tt o lk oad nceme o ow t id he s py mr hat r f fr incherod dombendautearol isheaveceerevy whra giololaton n asot dicouss lomant wigay ed tucatowofofuedo bt stiut fis d ime f ifil upoouthet bo imy s m ghed d un asc gh fallnishen masthabteppr meatand ye inomy f futhangh lire bira ta thecon t pon i che hon w he wa m athit oowourno therecee ave h buimots sthe t wop 1 asamadis a g che t httinyay andotempy thide tns t we s igherashindlatit atiounghisheienom herout fof st buratthacuhagou anden bexp h whilten tovao thesid anxagoumatherowa twopalirulicly chashepeps t onisthery izy urye d lastn frrabe thathedond b plulot e iors p botu ioulu andige lingequpy igea hi mrknds ar t ouge owaly hee s fe thiacutheansn